# Advanced Database Project
### Group 22
* Enzo Chatalov - fc54414
* Agnieszka Radomska - fc64357
* Duarte Gonçalves - fc64465
* Tommaso Tragno - fc64699

In [1]:
import pandas as pd
import json
import pymongo as pm
import mysql.connector
import time
from sqlalchemy import create_engine,text
from sqlalchemy.exc import PendingRollbackError
import kagglehub

## Configuration file

create a `config.json` file with the following structure:

```
{
    "mongo": {
        "username": "your_mongo_username",
        "password": "your_mongo_password",
        "host": "your_mongo_host",
        "port": "your_mongo_port"
    },
    "mysql": {
        "username": "your_mysql_username",
        "password": "your_mysql_password",
        "host": "your_mysql_host",
        "port": "your_mysql_port"
    }
}
```

In [2]:
# load configuration file with password for mongoDB and mySQL
with open('config.json', 'r') as f:
    config = json.load(f)

# Extract username and password for MongoDB and MySQL
mongo_username = config["mongo"]["username"]
mongo_password = config["mongo"]["password"]
mongo_host = config["mongo"]["host"]
mongo_port = config["mongo"]["port"]

mysql_username = config["mysql"]["username"]
mysql_password = config["mysql"]["password"]
mysql_host = config["mysql"]["host"]
mysql_port = config["mysql"]["port"]

In [3]:
# Download latest dataset version for books recommendation
# path = kagglehub.dataset_download("arashnic/book-recommendation-dataset")

# Manual path specification
path = './kagglehub/datasets/arashnic/book-recommendation-dataset/versions/3'

## Data validation
1. Load the `.csv` file from the path specified;
2. Drop the rows that do not contains a primary key
3. Fill the `na` cells with a predefined value
4. Drop eventualy doplicates
5. Convert the string data into the proper data type

In [4]:
# Load dataset into pandas dataframe
df_books = pd.read_csv(f'{path}/Books.csv')
df_ratings = pd.read_csv(f'{path}/Ratings.csv')
df_users = pd.read_csv(f'{path}/Users.csv')

print('Check NA values presence before data validation')
print(f'Books data frame: {df_books.isna().any().any()}')
print(f'Ratings data frame: {df_ratings.isna().any().any()}')
print(f'Users data frame: {df_users.isna().any().any()}')


df_users = df_users.dropna(subset=['User-ID'])
df_users = df_users.fillna({'Location': 'not available', 'Age': '0'})
df_books = df_books.dropna(subset=['ISBN'])
df_books = df_books.fillna({
    'Book-Title': 'not available', 
    'Book-Author': 'not available', 
    'Year-Of-Publication': '0',
    'Publisher': 'not available', 
    'Image-URL-S': 'not available', 
    'Image-URL-M': 'not available', 
    'Image-URL-L': 'not available'
})
df_ratings = df_ratings.dropna(subset=['User-ID', 'ISBN'])
df_ratings = df_ratings.fillna({'Book-Rating': '0'})

# Tu wlatuje FIX3
df_users = df_users.drop_duplicates()
df_books = df_books.drop_duplicates()
df_ratings = df_ratings.drop_duplicates()

# data type conversion
df_users['User-ID'] = pd.to_numeric(df_users['User-ID'], errors='coerce').fillna(0).astype(int)
df_users['Age'] = pd.to_numeric(df_users['Age'], errors='coerce').fillna(0).astype(int)

df_ratings['User-ID'] = pd.to_numeric(df_ratings['User-ID'], errors='coerce').fillna(0).astype(int)
df_ratings['Book-Rating'] = pd.to_numeric(df_ratings['Book-Rating'], errors='coerce').fillna(0).astype(int)

df_books['Year-Of-Publication'] = pd.to_numeric(df_books['Year-Of-Publication'], errors='coerce').fillna(0).astype(int)
df_books = df_books[df_books['ISBN'].apply(lambda x: x.isdigit())]


print('Check NA values presence after data validation')
print(f'Books data frame: {df_books.isna().any().any()}')
print(f'Ratings data frame: {df_ratings.isna().any().any()}')
print(f'Users data frame: {df_users.isna().any().any()}')

Check NA values presence before data validation
Books data frame: True
Ratings data frame: False
Users data frame: True
Check NA values presence after data validation
Books data frame: False
Ratings data frame: False
Users data frame: False


# MongoDB
## Connects and populate the No-SQL database

In [5]:
# Connect to MongoDB locally
client = pm.MongoClient(f'mongodb://{mongo_host}:{mongo_port}',
                              username = mongo_username,
                              password = mongo_password)

## Collection Structure

### Old Structrure 

In [6]:
def colletionStructure1_MongoDB():
    client.drop_database("project")
    db = client["project"]

    books = db["books"]
    ratings = db["ratings"]
    users = db["users"]

    start_time = time.time()
    books.insert_many(df_books.to_dict(orient="records"), ordered=False)
    ratings.insert_many(df_ratings.to_dict(orient="records"), ordered=False)
    users.insert_many(df_users.to_dict(orient="records"), ordered=False)

    # Add a new field to all documents in the 'books' collection
    books.update_many({}, {"$set": {"Global_Rating": 0.00}})
    endTime = time.time() - start_time
    print(f"Data inserted into MongoDB collections successfully in {endTime} seconds!")

    return endTime, books, ratings, users

mdbInsertion1, _, _ ,_ = colletionStructure1_MongoDB()

Data inserted into MongoDB collections successfully in 251.90109777450562 seconds!


### New Structure

In [7]:
def colletionStructure2_MongoDB():
    client.drop_database("project")
    db = client["project"]

    books = db["books"]
    ratings = db["ratings"]
    users = db["users"]

    # Prepare a dictionary to store book documents
    books_dict = {}

    # Iterate through the books DataFrame
    for _, book_row in df_books.iterrows():
        isbn = book_row['ISBN']
        
        # Initialize the book document
        books_dict[isbn] = {
            "isbn": isbn,
            "title": book_row['Book-Title'],
            "author": book_row['Book-Author'],
            "publisher": book_row['Publisher'],
            "year": int(book_row['Year-Of-Publication']),
            "global_rating": 0,  # Set a default global rating
            "images": {
                "small": book_row['Image-URL-S'],
                "medium": book_row['Image-URL-M'],
                "large": book_row['Image-URL-L']
            }
        }

    ratings_dict = {}    
    # Iterate through the ratings DataFrame
    for _, rating_row in df_ratings.iterrows():
        isbn = rating_row['ISBN'] 
        ratings_dict[isbn] = {
            "isbn": isbn,
            "user_id": rating_row['User-ID'],
            "rating": int(rating_row['Book-Rating'])
        }

    users_dict = {}
    # Iterate through the users DataFrame
    for _, user_row in df_users.iterrows():
        user_id = user_row['User-ID']
        users_dict[user_id] = {
            "user_id": user_id,
            "location": user_row['Location'],
            "age": int(user_row['Age'])
        }

    start_time = time.time()
    # Insert the documents into the books collection
    books.insert_many(list(books_dict.values()))
    users.insert_many(list(users_dict.values()))
    ratings.insert_many(list(ratings_dict.values()))
    endTime = time.time() - start_time

    print(f'Data successfully loaded into the MongoDB books collection in {endTime} seconds!')
    return endTime, books, ratings, users

mdbInsertion2, _, _ ,_ = colletionStructure2_MongoDB()

Data successfully loaded into the MongoDB books collection in 100.05192565917969 seconds!


### Comparation Times

In [8]:
comparison_table = pd.DataFrame([[mdbInsertion1, mdbInsertion2]], columns=["Old Structure", "New Option"], index=["Insertion Time"])
comparison_table.to_csv("InsertionStructureTimes.csv")
print(comparison_table)

# Determine the structure with the least insertion time
if mdbInsertion1 < mdbInsertion2:
    print("\nUsing the old structure as it takes less time.")
    mdbInsertion, books, ratings, users = colletionStructure1_MongoDB()
else:
    print("\nUsing the new structure as it takes less time.")
    mdbInsertion, books, ratings, users = colletionStructure2_MongoDB()

                Old Structure  New Option
Insertion Time     251.901098  100.051926

Using the new structure as it takes less time.
Data successfully loaded into the MongoDB books collection in 65.20647621154785 seconds!


## Queries
### Simple 
#### 1- All books published in the year 2000

In [9]:
"""year = 2000
start_time = time.time()
books_in_year = books.find({"Year-Of-Publication": year})
mdbSimple1 = time.time() - start_time
print(f"Total Number of Books Published in the year {year}: {books.count_documents({'Year-Of-Publication': year})}")
for book in books_in_year:
    bookTitle = book.get("Book-Title")
    bookISBN = book.get("ISBN")
    print(f"ISBN: {bookISBN}, Book Title: {bookTitle}")"""

'year = 2000\nstart_time = time.time()\nbooks_in_year = books.find({"Year-Of-Publication": year})\nmdbSimple1 = time.time() - start_time\nprint(f"Total Number of Books Published in the year {year}: {books.count_documents({\'Year-Of-Publication\': year})}")\nfor book in books_in_year:\n    bookTitle = book.get("Book-Title")\n    bookISBN = book.get("ISBN")\n    print(f"ISBN: {bookISBN}, Book Title: {bookTitle}")'

In [10]:
year = 2000
start_time = time.time()
books_in_year = books.find({"year": year})
mdbSimple1 = time.time() - start_time
print(f"Total Number of Books Published in the year {year}: {books.count_documents({'year': year})}")
for book in books_in_year:
    bookTitle = book.get("title")
    bookISBN = book.get("isbn")
    print(f"ISBN: {bookISBN}, Book Title: {bookTitle}")

Total Number of Books Published in the year 2000: 15748
ISBN: 0425176428, Book Title: What If?: The World's Foremost Military Historians Imagine What Might Have Been
ISBN: 0061076031, Book Title: Mary-Kate &amp; Ashley Switching Goals (Mary-Kate and Ashley Starring in)
ISBN: 0345417623, Book Title: Timeline
ISBN: 3442446937, Book Title: Tage der Unschuld.
ISBN: 0375406328, Book Title: Lying Awake
ISBN: 0553582909, Book Title: Icebound
ISBN: 0842342702, Book Title: Left Behind: A Novel of the Earth's Last Days (Left Behind #1)
ISBN: 0312970242, Book Title: The Angel Is Near
ISBN: 0375410538, Book Title: Anil's Ghost
ISBN: 0340767936, Book Title: Turning Thirty
ISBN: 0446677450, Book Title: Rich Dad, Poor Dad: What the Rich Teach Their Kids About Money--That the Poor and Middle Class Do Not!
ISBN: 0446608653, Book Title: The Alibi
ISBN: 0812575954, Book Title: The Deal
ISBN: 0671042858, Book Title: The Girl Who Loved Tom Gordon
ISBN: 1903019699, Book Title: The Soulbane Stratagem
ISBN: 0

#### 2- All users that are older than 30 years old

In [11]:
"""age = 30
start_time = time.time()
users_older_than_30 = users.find({"Age": {"$gt": age}})
mdbSimple2 = time.time() - start_time
print(f"Total Number of Users older than {age}: {users.count_documents({"Age": {"$gt": age}})}")
for user in users_older_than_30:
    userID = user.get("User-ID")
    print(f"User ID: {userID}")"""

'age = 30\nstart_time = time.time()\nusers_older_than_30 = users.find({"Age": {"$gt": age}})\nmdbSimple2 = time.time() - start_time\nprint(f"Total Number of Users older than {age}: {users.count_documents({"Age": {"$gt": age}})}")\nfor user in users_older_than_30:\n    userID = user.get("User-ID")\n    print(f"User ID: {userID}")'

In [12]:
age = 30
start_time = time.time()
users_older_than_30 = users.find({"age": {"$gt": age}})
mdbSimple2 = time.time() - start_time
print(f"Total Number of Users older than {age}: {users.count_documents({"age": {"$gt": age}})}")
for user in users_older_than_30:
    userID = user.get("user_id")
    print(f"User ID: {userID}")

Total Number of Users older than 30: 91816
User ID: 6
User ID: 21
User ID: 25
User ID: 27
User ID: 33
User ID: 38
User ID: 40
User ID: 44
User ID: 46
User ID: 51
User ID: 54
User ID: 63
User ID: 64
User ID: 67
User ID: 70
User ID: 72
User ID: 75
User ID: 85
User ID: 89
User ID: 90
User ID: 93
User ID: 94
User ID: 99
User ID: 100
User ID: 103
User ID: 104
User ID: 105
User ID: 112
User ID: 114
User ID: 117
User ID: 119
User ID: 124
User ID: 125
User ID: 129
User ID: 132
User ID: 133
User ID: 139
User ID: 144
User ID: 148
User ID: 157
User ID: 158
User ID: 164
User ID: 165
User ID: 168
User ID: 172
User ID: 174
User ID: 176
User ID: 177
User ID: 182
User ID: 189
User ID: 190
User ID: 191
User ID: 196
User ID: 199
User ID: 206
User ID: 210
User ID: 216
User ID: 218
User ID: 221
User ID: 228
User ID: 242
User ID: 245
User ID: 251
User ID: 252
User ID: 255
User ID: 259
User ID: 260
User ID: 261
User ID: 281
User ID: 284
User ID: 299
User ID: 301
User ID: 302
User ID: 308
User ID: 311
User I

### Complex
#### 1- Update all ratings from UserID "276641" to 8

In [13]:
"""userID = 276641
print("Ratings before the update:")
for rating in ratings.find({"User-ID": userID}):
        print(rating)

start_time = time.time()
ratings.update_many({"User-ID": userID}, {"$set": {"Book-Rating": 8}})
endTime = time.time() - start_time

print("Ratings after the update:")
for rating in ratings.find({"User-ID": userID}):
    print(rating)"""

'userID = 276641\nprint("Ratings before the update:")\nfor rating in ratings.find({"User-ID": userID}):\n        print(rating)\n\nstart_time = time.time()\nratings.update_many({"User-ID": userID}, {"$set": {"Book-Rating": 8}})\nendTime = time.time() - start_time\n\nprint("Ratings after the update:")\nfor rating in ratings.find({"User-ID": userID}):\n    print(rating)'

In [14]:
def complexQuery1_MongoDB():
    userID = 276641
    print("Ratings before the update:")
    for rating in ratings.find({"user_id": userID}):
        print(rating)

    start_time = time.time()
    ratings.update_many({"user_id": userID}, {"$set": {"rating": 8}})
    endTime = time.time() - start_time

    print("Ratings after the update:")
    for rating in ratings.find({"user_id": userID}):
        print(rating)

    return endTime

mdbComplex1_beforeIdx = complexQuery1_MongoDB()

Ratings before the update:
{'_id': ObjectId('675ea2cdb1ce8ecec0a2e966'), 'isbn': '0679776818', 'user_id': 276641, 'rating': 0}
{'_id': ObjectId('675ea2cdb1ce8ecec0a2eb16'), 'isbn': '0971880107', 'user_id': 276641, 'rating': 0}
{'_id': ObjectId('675ea2cdb1ce8ecec0a2eded'), 'isbn': '0440225442', 'user_id': 276641, 'rating': 0}
{'_id': ObjectId('675ea2cdb1ce8ecec0a2ef24'), 'isbn': '0316776963', 'user_id': 276641, 'rating': 0}
{'_id': ObjectId('675ea2cdb1ce8ecec0a2ef27'), 'isbn': '033031582', 'user_id': 276641, 'rating': 5}
{'_id': ObjectId('675ea2cdb1ce8ecec0a2ef39'), 'isbn': '0345413903', 'user_id': 276641, 'rating': 0}
{'_id': ObjectId('675ea2cdb1ce8ecec0a2efe2'), 'isbn': '0553571656', 'user_id': 276641, 'rating': 0}
{'_id': ObjectId('675ea2cdb1ce8ecec0a2efe6'), 'isbn': '0553574566', 'user_id': 276641, 'rating': 0}
{'_id': ObjectId('675ea2cdb1ce8ecec0a2f02a'), 'isbn': '0743444477', 'user_id': 276641, 'rating': 8}
{'_id': ObjectId('675ea2cdb1ce8ecec0a2f0d3'), 'isbn': '0385722206', 'user_

#### 2 - Add a new column in the Books table with the mean ratings of every book

##### Original Code

In [15]:
pipeline = [
    {
        "$group": {
            "_id": "$isbn",  # Group by ISBN
            "average_rating": {"$avg": "$rating"}  # Calculate the average rating
        }
    },
    {
        "$project": {
            "_id": 1,
            "average_rating": {"$round": ["$average_rating", 2]}  # Round to 2 decimal places
        }
    }
]

start = time.time()
average_ratings = list(ratings.aggregate(pipeline))

total_updates = len(average_ratings)
threshold = 5000
updated = 0

for i in range(0, total_updates, threshold):
    batch = average_ratings[i:i + threshold]
    
    # Perform updates only where the global_rating is different
    for record in batch:
        isbn = record["_id"]
        avg_rating = record["average_rating"]

        # Update only if the global rating is different
        books.update_one(
            {"isbn": isbn, "global_rating": {"$ne": avg_rating}}, 
            {"$set": {"global_rating": avg_rating}}
        )
        
    updated += len(batch)
    print(f"Updates Done: {updated}/{total_updates}, took {time.time() - start:.2f} seconds.")  

mdbComplex2_beforeIdx = time.time() - start    


Updates Done: 5000/340556, took 896.54 seconds.
Updates Done: 10000/340556, took 2050.68 seconds.
Updates Done: 15000/340556, took 2944.95 seconds.
Updates Done: 20000/340556, took 3826.39 seconds.
Updates Done: 25000/340556, took 4727.74 seconds.
Updates Done: 30000/340556, took 5630.95 seconds.
Updates Done: 35000/340556, took 6529.13 seconds.
Updates Done: 40000/340556, took 6758.95 seconds.
Updates Done: 45000/340556, took 6911.93 seconds.
Updates Done: 50000/340556, took 7065.02 seconds.
Updates Done: 55000/340556, took 7218.20 seconds.
Updates Done: 60000/340556, took 7371.28 seconds.
Updates Done: 65000/340556, took 7524.12 seconds.
Updates Done: 70000/340556, took 7676.90 seconds.
Updates Done: 75000/340556, took 7833.84 seconds.
Updates Done: 80000/340556, took 7999.15 seconds.
Updates Done: 85000/340556, took 8164.64 seconds.
Updates Done: 90000/340556, took 8329.97 seconds.
Updates Done: 95000/340556, took 8495.28 seconds.
Updates Done: 100000/340556, took 8660.93 seconds.
U

## Indexes

In [ ]:
ratings.create_index([("isbn", pm.ASCENDING)])
books.create_index([("isbn", pm.ASCENDING)])
users.create_index([("user_id", pm.ASCENDING)])

print(f'Index on ratings created: {ratings.index_information}')
print(f'Index on books created: {books.index_information}')
print(f'Index on users created: {users.index_information}')

Index on ratings created: <bound method Collection.index_information of Collection(Database(MongoClient(host=['clusterbda-shard-00-01.wkoq8.mongodb.net:27017', 'clusterbda-shard-00-02.wkoq8.mongodb.net:27017', 'clusterbda-shard-00-00.wkoq8.mongodb.net:27017'], document_class=dict, tz_aware=False, connect=True, authsource='admin', replicaset='atlas-5b7ugl-shard-0', tls=True), 'project'), 'ratings')>
Index on books created: <bound method Collection.index_information of Collection(Database(MongoClient(host=['clusterbda-shard-00-01.wkoq8.mongodb.net:27017', 'clusterbda-shard-00-02.wkoq8.mongodb.net:27017', 'clusterbda-shard-00-00.wkoq8.mongodb.net:27017'], document_class=dict, tz_aware=False, connect=True, authsource='admin', replicaset='atlas-5b7ugl-shard-0', tls=True), 'project'), 'books')>
Index on users created: <bound method Collection.index_information of Collection(Database(MongoClient(host=['clusterbda-shard-00-01.wkoq8.mongodb.net:27017', 'clusterbda-shard-00-02.wkoq8.mongodb.net:

In [19]:
def complexQuery2OG():
    pipeline = [
        {
            "$group": {
                "_id": "$isbn",  # Group by ISBN
                "average_rating": {"$avg": "$rating"}  # Calculate the average rating
            }
        },
        {
            "$project": {
                "_id": 1,
                "average_rating": {"$round": ["$average_rating", 2]}  # Round to 2 decimal places
            }
        }
    ]

    start = time.time()
    average_ratings = list(ratings.aggregate(pipeline))

    total_updates = len(average_ratings)
    threshold = 5000
    updated = 0

    for i in range(0, total_updates, threshold):
        batch = average_ratings[i:i + threshold]
        
        # Perform updates only where the global_rating is different
        for record in batch:
            isbn = record["_id"]
            avg_rating = record["average_rating"]

            # Update only if the global rating is different
            books.update_one(
                {"isbn": isbn, "global_rating": {"$ne": avg_rating}}, 
                {"$set": {"global_rating": avg_rating}}
            )
            
        updated += len(batch)
        print(f"Updates Done: {updated}/{total_updates}, took {time.time() - start:.2f} seconds.")  

    endTime = time.time() - start    
    return endTime

### Comparation Times Complex Queries - Original Version Before Index & After Index

In [20]:
mdbComplex1_afterIdx = complexQuery1_MongoDB()
mdbComplex2_1 = complexQuery2OG()

data = {
    "Complex Query 1 ": {"Before Index": mdbComplex1_beforeIdx, "After Index": mdbComplex1_afterIdx},
    "Complex Query 2 ": {"Before Index": mdbComplex2_beforeIdx, "After Index": mdbComplex2_1}
}


comparison_table = pd.DataFrame(data)
comparison_table.to_csv("MongoComplexQueriesIndexTimes.csv")
print(comparison_table)

Ratings before the update:
{'_id': ObjectId('675ea2cdb1ce8ecec0a2e966'), 'isbn': '0679776818', 'user_id': 276641, 'rating': 8}
{'_id': ObjectId('675ea2cdb1ce8ecec0a2eb16'), 'isbn': '0971880107', 'user_id': 276641, 'rating': 8}
{'_id': ObjectId('675ea2cdb1ce8ecec0a2eded'), 'isbn': '0440225442', 'user_id': 276641, 'rating': 8}
{'_id': ObjectId('675ea2cdb1ce8ecec0a2ef24'), 'isbn': '0316776963', 'user_id': 276641, 'rating': 8}
{'_id': ObjectId('675ea2cdb1ce8ecec0a2ef27'), 'isbn': '033031582', 'user_id': 276641, 'rating': 8}
{'_id': ObjectId('675ea2cdb1ce8ecec0a2ef39'), 'isbn': '0345413903', 'user_id': 276641, 'rating': 8}
{'_id': ObjectId('675ea2cdb1ce8ecec0a2efe2'), 'isbn': '0553571656', 'user_id': 276641, 'rating': 8}
{'_id': ObjectId('675ea2cdb1ce8ecec0a2efe6'), 'isbn': '0553574566', 'user_id': 276641, 'rating': 8}
{'_id': ObjectId('675ea2cdb1ce8ecec0a2f02a'), 'isbn': '0743444477', 'user_id': 276641, 'rating': 8}
{'_id': ObjectId('675ea2cdb1ce8ecec0a2f0d3'), 'isbn': '0385722206', 'user_

### Query 2 Optimization Option - Bulk Write with condition


In [21]:
def complexQuery2Opt():
    pipeline = [
        {
            "$group": {
                "_id": "$isbn",  # Group by ISBN
                "average_rating": {"$avg": "$rating"}  # Calculate the average rating
            }
        },
        {
            "$project": {
                "_id": 1,
                "average_rating": {"$round": ["$average_rating", 2]}  # Round to 2 decimal places
            }
        }
    ]

    start = time.time()
    average_ratings = list(ratings.aggregate(pipeline))
    total_updates = len(average_ratings)
    updates_done = 0
    threshold = 5000

    for i in range(0, total_updates, threshold):
        batch = average_ratings[i:i + threshold]
        bulk_ops = [
            pm.UpdateOne(
                {"isbn": item["_id"], "global_rating": {"$ne": avg_rating}},
                {"$set": {"global_rating": item["average_rating"]}}
            ) for item in batch
        ]

        if bulk_ops:
            books.bulk_write(bulk_ops)
            updates_done += len(batch)
            print(f"Updates Done: {updates_done}/{total_updates}, took {time.time() - start} seconds.")

    endTime = time.time() - start
    print(f"Global ratings added to the books collection successfully in {endTime} seconds.")
    return endTime

### Comparation Times Complex Query 2 - Original Version & Optimized Version

In [34]:
mdbComplex2_2 = complexQuery2Opt()

comparison_table = pd.DataFrame([[mdbComplex2_1, mdbComplex2_2]], columns=["Original Version", "Optimized Version"], index=["Query 2 Time"])
comparison_table.to_csv("MongoComplexQuery2AfterIndex.csv")
print(comparison_table)

# Determine the structure with the least insertion time
if mdbComplex2_1 < mdbComplex2_2:
    print("\nUsing the original version as it takes less time.")
    mdbComplex2_afterIdx = mdbComplex2_1
else:
    print("\nUsing the optimized version as it takes less time.")
    mdbComplex2_afterIdx = mdbComplex2_2

Updates Done: 5000/340556, took 8.19087529182434 seconds.
Updates Done: 10000/340556, took 11.385846853256226 seconds.
Updates Done: 15000/340556, took 13.412288188934326 seconds.
Updates Done: 20000/340556, took 15.389097452163696 seconds.
Updates Done: 25000/340556, took 17.41411328315735 seconds.
Updates Done: 30000/340556, took 19.39525818824768 seconds.
Updates Done: 35000/340556, took 22.396801233291626 seconds.
Updates Done: 40000/340556, took 26.39273238182068 seconds.
Updates Done: 45000/340556, took 28.398021697998047 seconds.
Updates Done: 50000/340556, took 34.40684533119202 seconds.
Updates Done: 55000/340556, took 40.524319648742676 seconds.
Updates Done: 60000/340556, took 46.63422131538391 seconds.
Updates Done: 65000/340556, took 50.84023094177246 seconds.
Updates Done: 70000/340556, took 52.850510120391846 seconds.
Updates Done: 75000/340556, took 54.841397285461426 seconds.
Updates Done: 80000/340556, took 56.84416937828064 seconds.
Updates Done: 85000/340556, took 5

# MySQL
## Connects to MySql database, create the schema and populate the tables

In [23]:
# Connect to mySQL locally
mydb = mysql.connector.connect(
    host=mysql_host,
    port=mysql_port,
    user=mysql_username,
    password=mysql_password
)

cursor = mydb.cursor()

In [24]:
cursor.execute("DROP DATABASE IF EXISTS project")

In [25]:
cursor.execute("CREATE DATABASE IF NOT EXISTS project")
cursor.execute("USE project")

cursor.execute("""
    CREATE TABLE IF NOT EXISTS users (
        user_id INT PRIMARY KEY,
        location VARCHAR(255),
        age INT
    )
""")

cursor.execute("""
    CREATE TABLE IF NOT EXISTS books (
        ISBN VARCHAR(20) PRIMARY KEY,
        Book_Title VARCHAR(255),
        Book_Author VARCHAR(255),
        Year_Of_Publication INT,
        Publisher VARCHAR(255),
        Image_URL_S VARCHAR(255),
        Image_URL_M VARCHAR(255),
        Image_URL_L VARCHAR(255),
        Global_Rating FLOAT
    )
""")

cursor.execute("""
    CREATE TABLE IF NOT EXISTS ratings (
        User_ID INT,
        ISBN VARCHAR(20),
        Book_Rating INT,
        FOREIGN KEY (User_ID) REFERENCES users(user_id),
        FOREIGN KEY (ISBN) REFERENCES books(ISBN),
        PRIMARY KEY (User_ID, ISBN)
    )
""")
start_time = time.time()
# added try - except statement to catch the problematic rows
for _, row in df_books.iterrows():
    try:
        cursor.execute(
            "INSERT IGNORE INTO books (ISBN, Book_Title, Book_Author, Year_Of_Publication, Publisher, Image_URL_S, Image_URL_M, Image_URL_L) VALUES (%s, %s, %s, %s, %s, %s, %s, %s)",
            (row['ISBN'], row['Book-Title'], row['Book-Author'], row['Year-Of-Publication'], row['Publisher'], row['Image-URL-S'], row['Image-URL-M'], row['Image-URL-L'])
        )
    except:
        print(row)

for _, row in df_users.iterrows():
    try:
        cursor.execute(
            "INSERT IGNORE INTO users (user_id, location, age) VALUES (%s, %s, %s)",
            (row['User-ID'], row['Location'], row['Age']) # Tutaj wleciał FIX1
        )
    except:
        print(row)

for _, row in df_ratings.iterrows():
    try:
        cursor.execute(
            "INSERT IGNORE INTO ratings (User_ID, ISBN, Book_Rating) VALUES (%s, %s, %s)",
            (row['User-ID'], row['ISBN'], row['Book-Rating'])
        )
    except:
        print(row)

mydb.commit()
sqlInsertion = time.time() - start_time

print("Data inserted successfully.")



Data inserted successfully.


## Queries
### Simple
#### 1- All books published in the year 2000

In [26]:
start_time = time.time()
cursor.execute("SELECT ISBN, Book_Title FROM books WHERE Year_Of_Publication = 2000")
sql_books_in_year = cursor.fetchall()
sqlSimple1 = time.time() - start_time
print(f'There are {len(sql_books_in_year)} users older than 30 years:')
for book in sql_books_in_year:
    bookTitle = book[1]
    bookISBN = book[0]
    print(f"ISBN: {bookISBN}, Book Title: {bookTitle}")

There are 15748 users older than 30 years:
ISBN: 0001047647, Book Title: First Among Equals
ISBN: 0001047663, Book Title: Matter Of Honour
ISBN: 0002000369, Book Title: Frederick Street: Living and Dying on Canada's Love Canal (Phyllis Bruce Books)
ISBN: 0002200813, Book Title: Lichens (New Naturalist)
ISBN: 0002200821, Book Title: Lichens (New Naturalist)
ISBN: 0002202107, Book Title: HOUSE DOCTOR
ISBN: 0002254131, Book Title: Acts of Betrayal
ISBN: 0002258382, Book Title: The Dragon Charmer
ISBN: 0002258560, Book Title: Is Shane MacGowan Still Alive?
ISBN: 0002261022, Book Title: The Glass Palace
ISBN: 0002261200, Book Title: The Coins of Judas
ISBN: 0002261529, Book Title: Temptation
ISBN: 0002326833, Book Title: Silent playgrounds
ISBN: 0003277585, Book Title: Economics Explained
ISBN: 0004489640, Book Title: Collins Ghost Hunters Great Britain
ISBN: 0004723708, Book Title: Mythology (Collins Gem)
ISBN: 0004724097, Book Title: Collins Gem Portuguese Dictionary English-Portuguese, P

#### 2- All users that are older than 30 years old

In [27]:
start_time = time.time()
cursor.execute("SELECT user_id FROM users WHERE age > 30")
sql_users_above_30 = cursor.fetchall()
sqlSimple2 = time.time() - start_time

print(f'There are {len(sql_users_above_30)} users older than 30 years:')
for user in sql_users_above_30:
    print(f"UserID: {user[0]}")

There are 91816 users older than 30 years:
UserID: 6
UserID: 21
UserID: 25
UserID: 27
UserID: 33
UserID: 38
UserID: 40
UserID: 44
UserID: 46
UserID: 51
UserID: 54
UserID: 63
UserID: 64
UserID: 67
UserID: 70
UserID: 72
UserID: 75
UserID: 85
UserID: 89
UserID: 90
UserID: 93
UserID: 94
UserID: 99
UserID: 100
UserID: 103
UserID: 104
UserID: 105
UserID: 112
UserID: 114
UserID: 117
UserID: 119
UserID: 124
UserID: 125
UserID: 129
UserID: 132
UserID: 133
UserID: 139
UserID: 144
UserID: 148
UserID: 157
UserID: 158
UserID: 164
UserID: 165
UserID: 168
UserID: 172
UserID: 174
UserID: 176
UserID: 177
UserID: 182
UserID: 189
UserID: 190
UserID: 191
UserID: 196
UserID: 199
UserID: 206
UserID: 210
UserID: 216
UserID: 218
UserID: 221
UserID: 228
UserID: 242
UserID: 245
UserID: 251
UserID: 252
UserID: 255
UserID: 259
UserID: 260
UserID: 261
UserID: 281
UserID: 284
UserID: 299
UserID: 301
UserID: 302
UserID: 308
UserID: 311
UserID: 317
UserID: 319
UserID: 320
UserID: 328
UserID: 331
UserID: 332
UserID: 3

### Complex
#### 1- Update all ratings from UserID "276641" to 8

In [28]:
def complexQuery1_MySQL():
    userID = 276641
    new_rating = 8

    print("Ratings before the update:")
    cursor.execute("SELECT * FROM ratings WHERE User_ID = %s", (userID,))
    for rating in cursor.fetchall():
        print(rating)

    start_time = time.time()
    cursor.execute("UPDATE ratings SET Book_Rating = %s WHERE User_ID = %s", (new_rating, userID))
    mydb.commit()
    endTime = time.time() - start_time

    print("Ratings after the update:")
    cursor.execute("SELECT * FROM ratings WHERE User_ID = %s", (userID,))
    for rating in cursor.fetchall():
        print(rating)

    print(f"Ratings updated successfully in {endTime} seconds.")
    return endTime

sqlComplex1_beforeIdx = complexQuery1_MySQL()

Ratings before the update:
(276641, '0060928611', 8)
(276641, '0062502182', 0)
(276641, '0140039236', 0)
(276641, '0140250948', 6)
(276641, '0140258345', 0)
(276641, '0140265988', 0)
(276641, '0151006555', 0)
(276641, '0312254180', 0)
(276641, '0312311354', 8)
(276641, '0312420196', 6)
(276641, '0312952716', 8)
(276641, '0312979487', 9)
(276641, '0316776963', 0)
(276641, '0330306529', 0)
(276641, '0345337662', 0)
(276641, '0345386132', 7)
(276641, '0345404793', 8)
(276641, '0345413903', 0)
(276641, '0345447840', 8)
(276641, '0374254303', 0)
(276641, '0375414290', 8)
(276641, '0375507493', 6)
(276641, '0375508546', 0)
(276641, '0375758992', 7)
(276641, '0380603438', 0)
(276641, '0380713802', 0)
(276641, '0380975920', 0)
(276641, '0385319207', 0)
(276641, '0385722206', 7)
(276641, '0399149708', 0)
(276641, '0425108589', 9)
(276641, '0425164403', 0)
(276641, '0425184234', 0)
(276641, '0440225442', 0)
(276641, '0440234743', 6)
(276641, '0440236177', 8)
(276641, '0446359408', 0)
(276641, '0

### 2 - Add a new column in the Books table with the mean ratings of every book

In [29]:
def complexQuery2_MySQL():
    start_time = time.time()
    cursor.execute("""
        SELECT 
            ISBN, 
            ROUND(AVG(`Book_Rating`), 2) AS average_rating
        FROM ratings
        GROUP BY ISBN
    """)

    # Fetch all results
    average_ratings = cursor.fetchall()

    # Update the books table with the Global_Rating
    update_query = """
        UPDATE books 
        SET Global_Rating = %s 
        WHERE ISBN = %s
    """

    for isbn, avg_rating in average_ratings:
        cursor.execute(update_query, (avg_rating, isbn))

    # Commit the changes
    mydb.commit()
    endTime = time.time() - start_time
    print(f"Ratings updated successfully in {endTime} seconds.")
    return endTime

sqlComplex2_beforeIdx1 = complexQuery2_MySQL()

Ratings updated successfully in 38.87986946105957 seconds.


### Query Optimization

In [30]:
def complexQuery2Opt_MySQL():
    update_query = """
        UPDATE books b
        JOIN(
            SELECT 
                ISBN, 
                ROUND(AVG(`Book_Rating`), 2) AS average_rating
            FROM ratings
            GROUP BY ISBN
        ) r ON b.ISBN = r.ISBN
        SET b.Global_Rating = r.average_rating
    """

    start_time = time.time()
    cursor.execute(update_query)
    mydb.commit()
    endTime = time.time() - start_time
    print(f"Ratings updated successfully in {endTime} seconds.")
    return endTime

sqlComplex2_beforeIdx2 = complexQuery2Opt_MySQL()

Ratings updated successfully in 6.249463796615601 seconds.


In [35]:
if sqlComplex2_beforeIdx1 < sqlComplex2_beforeIdx2:
    print("\nUsing the original version as it takes less time.")
    sqlComplex2_beforeIdx = sqlComplex2_beforeIdx1
else:
    print("\nUsing the optimized version as it takes less time.")
    sqlComplex2_beforeIdx = sqlComplex2_beforeIdx2


Using the optimized version as it takes less time.


## Indexes

In [31]:
cursor.execute("CREATE INDEX idx_book ON books(ISBN)")
cursor.execute("CREATE INDEX idx_ratings ON ratings(ISBN)")
cursor.execute("CREATE INDEX idx_user ON users(user_ID)")
print('Index added ')

Index added 


#### Comparation Times Complex Queries

In [36]:
sqlComplex1_afterIdx = complexQuery1_MySQL()
sqlComplex2_afterIdx1 = complexQuery2_MySQL()
sqlComplex2_afterIdx2 = complexQuery2Opt_MySQL()

data = {
    "Complex Query 1 ": {"Before Index": sqlComplex1_beforeIdx, "After Index": sqlComplex1_afterIdx},
    "Complex Query 2 (Original Version)": {"Before Index": sqlComplex2_beforeIdx1, "After Index": sqlComplex2_afterIdx1},
    "Complex Query 2 (Optimized Version)": {"Before Index": sqlComplex2_beforeIdx2, "After Index": sqlComplex2_afterIdx2}
}

comparison_table = pd.DataFrame(data)
comparison_table.to_csv("MySQLComplexQueriesIndexTimes.csv")
print(comparison_table)

if sqlComplex2_afterIdx1 < sqlComplex2_afterIdx2:
    print("\nUsing the original version as it takes less time.")
    sqlComplex2_afterIdx = sqlComplex2_afterIdx1
else:
    print("\nUsing the optimized version as it takes less time.")
    sqlComplex2_afterIdx = sqlComplex2_afterIdx2

Ratings before the update:
(276641, '0060928611', 8)
(276641, '0062502182', 8)
(276641, '0140039236', 8)
(276641, '0140250948', 8)
(276641, '0140258345', 8)
(276641, '0140265988', 8)
(276641, '0151006555', 8)
(276641, '0312254180', 8)
(276641, '0312311354', 8)
(276641, '0312420196', 8)
(276641, '0312952716', 8)
(276641, '0312979487', 8)
(276641, '0316776963', 8)
(276641, '0330306529', 8)
(276641, '0345337662', 8)
(276641, '0345386132', 8)
(276641, '0345404793', 8)
(276641, '0345413903', 8)
(276641, '0345447840', 8)
(276641, '0374254303', 8)
(276641, '0375414290', 8)
(276641, '0375507493', 8)
(276641, '0375508546', 8)
(276641, '0375758992', 8)
(276641, '0380603438', 8)
(276641, '0380713802', 8)
(276641, '0380975920', 8)
(276641, '0385319207', 8)
(276641, '0385722206', 8)
(276641, '0399149708', 8)
(276641, '0425108589', 8)
(276641, '0425164403', 8)
(276641, '0425184234', 8)
(276641, '0440225442', 8)
(276641, '0440234743', 8)
(276641, '0440236177', 8)
(276641, '0446359408', 8)
(276641, '0

Ratings updated successfully in 31.633495330810547 seconds.
Ratings updated successfully in 6.008695602416992 seconds.
              Complex Query 1   Complex Query 2 (Original Version)  \
Before Index          0.034298                           38.879869   
After Index           0.000558                           31.633495   

              Complex Query 2 (Optimized Version)  
Before Index                             6.249464  
After Index                              6.008696  

Using the optimized version as it takes less time.


# Time Comparison

In [38]:
query_times = {
    "Insertion": {"MongoDB": mdbInsertion, "MySQL": sqlInsertion},
    "Simple Query 1": {"MongoDB": mdbSimple1, "MySQL": sqlSimple1},
    "Simple Query 2": {"MongoDB": mdbSimple2, "MySQL": sqlSimple2},
    "Complex Query 1 (Before Index)": {"MongoDB": mdbComplex1_beforeIdx, "MySQL": sqlComplex1_beforeIdx},
    "Complex Query 1 (After Index)": {"MongoDB": mdbComplex1_afterIdx, "MySQL": sqlComplex1_afterIdx},
    "Complex Query 2 (Before Index)": {"MongoDB": mdbComplex2_beforeIdx, "MySQL": sqlComplex2_beforeIdx},
    "Complex Query 2 (After Index)": {"MongoDB": mdbComplex2_afterIdx, "MySQL": sqlComplex2_afterIdx}
}


comparison_table = pd.DataFrame(query_times)
comparison_table.to_csv("comparison_tableV2.csv")
print(comparison_table)

          Insertion  Simple Query 1  Simple Query 2  \
MongoDB   65.206476        0.000078        0.000129   
MySQL    416.297687        0.889628        0.106730   

         Complex Query 1 (Before Index)  Complex Query 1 (After Index)  \
MongoDB                        0.427493                       0.387271   
MySQL                          0.034298                       0.000558   

         Complex Query 2 (Before Index)  Complex Query 2 (After Index)  
MongoDB                    16389.287529                     233.667583  
MySQL                          6.249464                       6.008696  
